In [13]:
import gymnasium as gym
from pogema import GridConfig
import pogema
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline


GRID_LEN = 18

def custom_step(self, action: list):
        assert len(action) == self.grid_config.num_agents
        rewards = []

        terminated = []

        self.move_agents(action)
        self.update_was_on_goal()

        for agent_idx in range(self.grid_config.num_agents):

            c_x, c_y = self.grid.positions_xy[agent_idx]
            f_x, f_y = self.grid.finishes_xy[agent_idx]

            #d = math.sqrt((c_x - f_x) ** 2 + (c_y - f_y) ** 2)    
            #reward = 1 - (d / (math.sqrt(2) * GRID_LEN))
            reward = 1 - ( (abs(c_x - f_x) + abs(c_y - f_y)) / (2 * GRID_LEN) )
            #print(f"[CURR] {c_x}, {c_y} [FINISH] {f_x}, {f_y} [DIST] {d} [REWARD] {reward}")


            on_goal = self.grid.on_goal(agent_idx)
            if on_goal and self.grid.is_active[agent_idx]:
                print("FINISH", reward)
                rewards.append(reward)
            else:
                rewards.append(reward)
            terminated.append(on_goal)

        for agent_idx in range(self.grid_config.num_agents):
            if self.grid.on_goal(agent_idx):
                self.grid.hide_agent(agent_idx)
                self.grid.is_active[agent_idx] = False

        infos = self._get_infos()

        observations = self._obs()
        truncated = [False] * self.grid_config.num_agents
        return observations, rewards, terminated, truncated, infos

pogema.envs.Pogema.step = custom_step

grid_config = GridConfig(
    size=8,
    density=0.3,
    num_agents=1,
    max_episode_steps=64,
    obs_radius=5
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [14]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(5.0e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


[I 2023-11-10 16:33:13,792] A new study created in memory with name: no-name-8065526f-b2cc-4b29-8e84-7dd89e8106bc
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
FINISH 1.0
FINISH 1.0
FINISH 1.0
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 53.7      |
|    ep_rew_mean        | 45.6      |
| time/                 |           |
|    fps                | 221       |
|    iterations         | 100       |
|    time_elapsed       | 2         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -7.28e-31 |
|    explained_variance | 0         |
|    learning_rate      | 0.739     |
|    n_updates          | 99        |
|    policy_loss        | -0        |
|    value_loss      

[I 2023-11-10 17:17:48,502] Trial 0 finished with value: 30.407407333333335 and parameters: {'gamma': 0.004494871948497582, 'lr': 0.7392028479046565}. Best is trial 0 with value: 30.407407333333335.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 49.1      |
|    ep_rew_mean        | 41.4      |
| time/                 |           |
|    fps                | 166       |
|    iterations         | 89000     |
|    time_elapsed       | 2674      |
|    total_timesteps    | 445000    |
| train/                |           |
|    entropy_loss       | -7.28e-09 |
|    explained_variance | 5.96e-08  |
|    learning_rate      | 0.0424    |
|    n_updates          | 88999     |
|    policy_loss        | -0        |
|    value_loss         | 0.000472  |
-------------------------------------
FINISH 1.0
FINISH 1.0
FINISH 1.0
FINISH 1.0
FINISH 1.0
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 57.8      |
|    ep_rew_mean        | 48.8      |
| time/                 |           |
|    fps                | 166       |
|    iterations         | 89100     |
|    time_elapsed       | 2676   

[I 2023-11-10 17:21:04,926] Trial 3 finished with value: 37.99074066666667 and parameters: {'gamma': 0.00013182443597851152, 'lr': 0.3956481588525515}. Best is trial 3 with value: 37.99074066666667.


FINISH 1.0
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 51.6      |
|    ep_rew_mean        | 43.4      |
| time/                 |           |
|    fps                | 173       |
|    iterations         | 99600     |
|    time_elapsed       | 2871      |
|    total_timesteps    | 498000    |
| train/                |           |
|    entropy_loss       | -5.49e-09 |
|    explained_variance | 0         |
|    learning_rate      | 0.0424    |
|    n_updates          | 99599     |
|    policy_loss        | -0        |
|    value_loss         | 0.199     |
-------------------------------------
FINISH 1.0
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 55.4      |
|    ep_rew_mean        | 46.6      |
| time/                 |           |
|    fps                | 173       |
|    iterations         | 99700     |
|    time_elapsed       | 2872      |
|    total_timesteps    | 49

[I 2023-11-10 17:21:08,810] Trial 1 finished with value: 51.15740733333333 and parameters: {'gamma': 0.0011933628640553686, 'lr': 0.05127089437780035}. Best is trial 1 with value: 51.15740733333333.


-------------------------------------
| eval/                 |           |
|    mean_ep_length     | 64        |
|    mean_reward        | 53.9      |
| time/                 |           |
|    total_timesteps    | 500000    |
| train/                |           |
|    entropy_loss       | -5.41e-09 |
|    explained_variance | 0         |
|    learning_rate      | 0.0424    |
|    n_updates          | 99999     |
|    policy_loss        | -0        |
|    value_loss         | 0.00464   |
-------------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 54       |
|    ep_rew_mean     | 45.8     |
| time/              |          |
|    fps             | 173      |
|    iterations      | 100000   |
|    time_elapsed    | 2875     |
|    total_timesteps | 500000   |
---------------------------------


[I 2023-11-10 17:21:08,984] Trial 2 finished with value: 53.93518533333333 and parameters: {'gamma': 0.012905465034043844, 'lr': 0.04241090469851767}. Best is trial 2 with value: 53.93518533333333.


Number of finished trials:  4
Best trial:
  Value:  53.93518533333333
  Params: 
    gamma: 0.012905465034043844
    lr: 0.04241090469851767
  User attrs:
    gamma: 0.9870945349659561


### Train agent with best hyper parameters

In [15]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.012905465034043844,#0.0001747891704351033,
    learning_rate=0.04241090469851767#0.02847505337754138,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [16]:
# Train agent and save it
a2c_model.learn(int(5.0e5))
a2c_model.save("saved/a2c_d")

FINISH 1.0
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 56.1     |
|    ep_rew_mean        | 46.5     |
| time/                 |          |
|    fps                | 1009     |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -4.6e-12 |
|    explained_variance | 3.7e-06  |
|    learning_rate      | 0.0424   |
|    n_updates          | 99       |
|    policy_loss        | -0       |
|    value_loss         | 3.56e-06 |
------------------------------------
FINISH 1.0
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 56.6      |
|    ep_rew_mean        | 48        |
| time/                 |           |
|    fps                | 1029      |
|    iterations         | 200       |
|    time_elapsed       | 0         |
|    total_timesteps    | 1000      |
| train

#### Testing 

In [17]:
a2c_model = A2C.load("saved/a2c_d")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


FINISH 1.0
FINISH 1.0
mean_reward:47.54 +/- 16.19


In [18]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 64
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
4 64 0 False
4 63 0 False
4 62 0 False
4 61 0 False
4 60 0 False
4 59 0 False
4 58 0 False
4 57 0 False
4 56 0 False
4 55 0 False
4 54 0 False
4 53 0 False
4 52 0 False
4 51 0 False
4 50 0 False
4 49 0 False
4 48 0 False
4 47 0 False
4 46 0 False
4 45 0 False
4 44 0 False
4 43 0 False
4 42 0 False
4 41 0 False
4 40 0 False
4 39 0 False
4 38 0 False
4 37 0 False
4 36 0 False
4 35 0 False
4 34 0 False
4 33 0 False
4 32 0 False
4 31 0 False
4 30 0 False
4 29 0 False
4 28 0 False
4 27 0 False
4 26 0 False
4 25 0 False
4 24 0 False
4 23 0 False
4 22 0 False
4 21 0 False
4 20 0 False
4 19 0 False
4 18 0 False
4 17 0 False
4 16 0 False
4 15 0 False
4 14 0 False
4 13 0 False
4 12 0 False
4 11 0 False
4 10 0 False
4 9 0 False
4 8 0 False
4 7 0 False
4 6 0 False
4 5 0 False
4 4 0 False
4 3 0 False
4 2 0 False
4 1 0 False
---1---
4 64 0 False
4 63 0 False
4 62 0 False
4 61 0 False
4 60 0 False
4 59 0 False
4 58 0 False
4 57 0 False
4 56 0 False
4 55 0 False
4 54 0 False
4 53 0 False
4 52 

In [19]:
step_array

[3,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 3,
 3,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 2,
 1,
 1,
 3,
 1,
 2,
 1,
 1,
 1,
 5,
 2,
 1,
 1,
 2,
 3,
 4,
 2,
 1,
 3,
 1,
 4,
 1,
 4,
 1,
 2,
 1,
 3,
 1,
 1,
 1,
 2,
 3,
 2]

In [23]:
import numpy as np
np.mean(step_array)

1.6333333333333333